In [13]:
import h5py
import pandas as pd
from pathlib import Path
import SomnoMed as som
import numpy as np

import sys
import os

sys.path.append('../som-gcnn/data/')

from pg import PGManager
from undercut_depth_v3 import find_undercut_depth
import datetime

# h5py.run_tests()

In [14]:
with PGManager(host='10.10.10.19', database='som_retention', password='rd_root_passwd') as pg:
    arch_retention_values_df = pd.read_sql('select filename, peak_value from retention_graph_labelling_results', pg.connection)
    retention_values_filenames_df = pd.read_sql('select case_id, side, image_filename_hashed_anterior from retention_graph_labelling_files', pg.connection)

df_merge = retention_values_filenames_df.merge(arch_retention_values_df, left_on='image_filename_hashed_anterior', right_on='filename', how='inner')
df_merge.head(10000)

/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


case_id   side image_filename_hashed_anterior  \
0     POUSA0102427  lower           1d04b73bf9e350d0.bmp   
1         DE138339  upper           2326184d400c33cd.bmp   
2     POAUS0033453  lower           1d866ce279946ea0.bmp   
3     POAUS0033524  upper           2d971f16de857015.bmp   
4         nl048662  upper           7c817dfca584db1f.bmp   
...            ...    ...                            ...   
9995  POUSA0101414  upper           6f65c096c187d608.bmp   
9996  POUSA0101321  lower           0e959fc013597c5f.bmp   
9997  POUSA0101525  upper           3d9fb1f4bae3278e.bmp   
9998  POUSA0101429  upper           0fe7b89108833018.bmp   
9999  POUSA0101529  upper           6a06e4e6b8904801.bmp   

                  filename  peak_value  
0     1d04b73bf9e350d0.bmp       144.0  
1     2326184d400c33cd.bmp       111.0  
2     1d866ce279946ea0.bmp        42.5  
3     2d971f16de857015.bmp        56.0  
4     7c817dfca584db1f.bmp        81.5  
...                    ...         ...  
9995  6f65c096c187d608.bmp        75.2  
9996  0e959fc013597c5f.bmp       101.0  
9997  3d9fb1f4bae3278e.bmp        77.0  
9998  0fe7b89108833018.bmp        82.0  
9999  6a06e4e6b8904801.bmp        73.5  

[10000 rows x 5 columns]

In [15]:
# %%time
with PGManager(host='10.10.10.19', database='som_retention', password='rd_root_passwd') as pg:
    arch_metadata_df = pd.read_sql('select * from arch_metadata', pg.connection)
    arch_files_df = pd.read_sql('select case_id, side, arch_cad_stage_2, relative_directory from arch_files', pg.connection)
    feature_files_df = pd.read_sql('select case_id, side, arch_cad_fit from feature_files', pg.connection)
    arch_retention_values_df =  pd.read_sql('select case_id, side, first_cam_retention_anterior from arch_retention_values', pg.connection)
    graph_retention_values_df = pd.read_sql('select filename, peak_value from retention_graph_labelling_results', pg.connection)
    retention_values_filenames_df = pd.read_sql('select case_id, side, image_filename_hashed_anterior from retention_graph_labelling_files', pg.connection)
    retention_values_df = retention_values_filenames_df.merge(graph_retention_values_df, left_on='image_filename_hashed_anterior', right_on='filename', how='inner')
    #arch_retention_coordinates_df = pd.read_sql('select * from arch_retention_coordinates where hole_search_failed = false and coords_verified = true', pg.connection)

raw_df = arch_metadata_df.merge(arch_files_df, on=['case_id', 'side']).merge(feature_files_df, on=['case_id', 'side']).merge(retention_values_df, on=['case_id', 'side']).merge(arch_retention_values_df, on=['case_id', 'side'])
raw_df

/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string

case_id   side first_cam_retention_date         product country  \
0           SE57420  lower               2021-12-02           avant      SE   
1          nl181217  lower               2022-04-11           avant     NLD   
2         NLD183727  upper               2022-04-11           avant     NLD   
3          nl181204  lower               2022-04-11           avant     NLD   
4           FI13617  upper               2022-04-11           avant      FI   
...             ...    ...                      ...             ...     ...   
16380  POUSA0087349  lower               2021-08-21  herbst_advance     USA   
16381  POUSA0087345  upper               2021-08-21  herbst_advance     USA   
16382  POUSA0087390  upper               2021-08-21  herbst_advance     USA   
16383  POUSA0087390  lower               2021-08-21  herbst_advance     USA   
16384  POUSA0087329  lower               2021-08-21  herbst_advance     USA   

             batch       arch_cad_stage_2  \
0      46020211126       SE57420 {L2}.stl   
1      31020220401      NL181217 {L2}.stl   
2      31020220401     NLD183727 {U2}.stl   
3      31020220401      NL181204 {L2}.stl   
4      35820220401       FI13617 {U2}.stl   
...            ...                    ...   
16380     10017211  POUSA0087349 {L2}.stl   
16381     10017211  POUSA0087345 {U2}.stl   
16382     10017214  POUSA0087390 {U2}.stl   
16383     10017214  POUSA0087390 {L2}.stl   
16384     10017210  POUSA0087329 {L2}.stl   

                                      relative_directory  \
0                avant/2021-12-02/SE/46020211126/SE57420   
1              avant/2022-04-11/NLD/31020220401/nl181217   
2             avant/2022-04-11/NLD/31020220401/NLD183727   
3              avant/2022-04-11/NLD/31020220401/nl181204   
4                avant/2022-04-11/FI/35820220401/FI13617   
...                                                  ...   
16380  herbst_advance/2021-08-21/USA/10017211/POUSA00...   
16381  herbst_advance/2021-08-21/USA/10017211/POUSA00...   
16382  herbst_advance/2021-08-21/USA/10017214/POUSA00...   
16383  herbst_advance/2021-08-21/USA/10017214/POUSA00...   
16384  herbst_advance/2021-08-21/USA/10017210/POUSA00...   

                                  arch_cad_fit image_filename_hashed_anterior  \
0           features/SE57420_lower_cad_fit.stl           4c9586522562c3af.bmp   
1          features/nl181217_lower_cad_fit.stl           0b98b3eaae2c53dc.bmp   
2         features/NLD183727_upper_cad_fit.stl           14299bb11eb394c5.bmp   
3          features/nl181204_lower_cad_fit.stl           27b2b76a5afda8aa.bmp   
4           features/FI13617_upper_cad_fit.stl           7137fc9aa74e2e67.bmp   
...                                        ...                            ...   
16380  features/POUSA0087349_lower_cad_fit.stl           29ca96911ed0f7b0.bmp   
16381  features/POUSA0087345_upper_cad_fit.stl           02a7079735ce6134.bmp   
16382  features/POUSA0087390_upper_cad_fit.stl           6eb53f0fe35c8376.bmp   
16383  features/POUSA0087390_lower_cad_fit.stl           0c0006fd4405f357.bmp   
16384  features/POUSA0087329_lower_cad_fit.stl           593fa66c0284a2f0.bmp   

                   filename  peak_value  first_cam_retention_anterior  
0      4c9586522562c3af.bmp        38.5                       37.7826  
1      0b98b3eaae2c53dc.bmp        57.0                       54.0590  
2      14299bb11eb394c5.bmp        51.0                       49.0853  
3      27b2b76a5afda8aa.bmp        63.0                       60.6292  
4      7137fc9aa74e2e67.bmp        70.2                       67.3373  
...                     ...         ...                           ...  
16380  29ca96911ed0f7b0.bmp        64.0                       57.2841  
16381  02a7079735ce6134.bmp        29.5                       21.7364  
16382  6eb53f0fe35c8376.bmp        44.0                       36.8435  
16383  0c0006fd4405f357.bmp        35.5                       28.8800  
16384  593fa66c0284a2f0.bmp        3

In [16]:
cols = list(raw_df.columns)
# cols.remove('arch_scan')
df = raw_df.dropna(subset=cols)
print(f"dropped {len(raw_df)-len(df)} arches")
df.reset_index(inplace=True, drop=True)
df

dropped 210 arches


case_id   side first_cam_retention_date         product country  \
0           SE57420  lower               2021-12-02           avant      SE   
1          nl181217  lower               2022-04-11           avant     NLD   
2         NLD183727  upper               2022-04-11           avant     NLD   
3          nl181204  lower               2022-04-11           avant     NLD   
4           FI13617  upper               2022-04-11           avant      FI   
...             ...    ...                      ...             ...     ...   
16170  POUSA0087349  lower               2021-08-21  herbst_advance     USA   
16171  POUSA0087345  upper               2021-08-21  herbst_advance     USA   
16172  POUSA0087390  upper               2021-08-21  herbst_advance     USA   
16173  POUSA0087390  lower               2021-08-21  herbst_advance     USA   
16174  POUSA0087329  lower               2021-08-21  herbst_advance     USA   

             batch       arch_cad_stage_2  \
0      46020211126       SE57420 {L2}.stl   
1      31020220401      NL181217 {L2}.stl   
2      31020220401     NLD183727 {U2}.stl   
3      31020220401      NL181204 {L2}.stl   
4      35820220401       FI13617 {U2}.stl   
...            ...                    ...   
16170     10017211  POUSA0087349 {L2}.stl   
16171     10017211  POUSA0087345 {U2}.stl   
16172     10017214  POUSA0087390 {U2}.stl   
16173     10017214  POUSA0087390 {L2}.stl   
16174     10017210  POUSA0087329 {L2}.stl   

                                      relative_directory  \
0                avant/2021-12-02/SE/46020211126/SE57420   
1              avant/2022-04-11/NLD/31020220401/nl181217   
2             avant/2022-04-11/NLD/31020220401/NLD183727   
3              avant/2022-04-11/NLD/31020220401/nl181204   
4                avant/2022-04-11/FI/35820220401/FI13617   
...                                                  ...   
16170  herbst_advance/2021-08-21/USA/10017211/POUSA00...   
16171  herbst_advance/2021-08-21/USA/10017211/POUSA00...   
16172  herbst_advance/2021-08-21/USA/10017214/POUSA00...   
16173  herbst_advance/2021-08-21/USA/10017214/POUSA00...   
16174  herbst_advance/2021-08-21/USA/10017210/POUSA00...   

                                  arch_cad_fit image_filename_hashed_anterior  \
0           features/SE57420_lower_cad_fit.stl           4c9586522562c3af.bmp   
1          features/nl181217_lower_cad_fit.stl           0b98b3eaae2c53dc.bmp   
2         features/NLD183727_upper_cad_fit.stl           14299bb11eb394c5.bmp   
3          features/nl181204_lower_cad_fit.stl           27b2b76a5afda8aa.bmp   
4           features/FI13617_upper_cad_fit.stl           7137fc9aa74e2e67.bmp   
...                                        ...                            ...   
16170  features/POUSA0087349_lower_cad_fit.stl           29ca96911ed0f7b0.bmp   
16171  features/POUSA0087345_upper_cad_fit.stl           02a7079735ce6134.bmp   
16172  features/POUSA0087390_upper_cad_fit.stl           6eb53f0fe35c8376.bmp   
16173  features/POUSA0087390_lower_cad_fit.stl           0c0006fd4405f357.bmp   
16174  features/POUSA0087329_lower_cad_fit.stl           593fa66c0284a2f0.bmp   

                   filename  peak_value  first_cam_retention_anterior  
0      4c9586522562c3af.bmp        38.5                       37.7826  
1      0b98b3eaae2c53dc.bmp        57.0                       54.0590  
2      14299bb11eb394c5.bmp        51.0                       49.0853  
3      27b2b76a5afda8aa.bmp        63.0                       60.6292  
4      7137fc9aa74e2e67.bmp        70.2                       67.3373  
...                     ...         ...                           ...  
16170  29ca96911ed0f7b0.bmp        64.0                       57.2841  
16171  02a7079735ce6134.bmp        29.5                       21.7364  
16172  6eb53f0fe35c8376.bmp        44.0                       36.8435  
16173  0c0006fd4405f357.bmp        35.5                       28.8800  
16174  593fa66c0284a2f0.bmp        3

In [36]:
# Split dataset
df_1 = df[df.first_cam_retention_anterior > df.peak_value * 0.9]
df_2 = df[df.first_cam_retention_anterior < df.peak_value * 1.1]
cols_to_use = df_1.columns.difference(df_2.columns)
df_12 = df_1.merge(df_2, on=['case_id', 'side'], suffixes=('', '_y'))
df_12.drop(df_12.filter(regex='_y$').columns.tolist(),axis=1, inplace=True)
print(df.describe())
print(df_12.describe())
df = df_12
df = pd.concat([df[df.peak_value<70], df[df.peak_value>103]])
df = df.sample(frac=1).reset_index(drop=True)
df

        peak_value  first_cam_retention_anterior
count  8864.000000                   8864.000000
mean     94.582796                     92.467433
std      45.577503                     45.122955
min       9.300000                      8.996570
25%      56.500000                     54.762500
50%     103.500000                     95.928250
75%     127.000000                    123.887500
max     330.000000                    328.810000
        peak_value  first_cam_retention_anterior
count  8864.000000                   8864.000000
mean     94.582796                     92.467433
std      45.577503                     45.122955
min       9.300000                      8.996570
25%      56.500000                     54.762500
50%     103.500000                     95.928250
75%     127.000000                    123.887500
max     330.000000                    328.810000


case_id   side first_cam_retention_date         product country  \
0     POUSA0104682  upper               2022-02-16  herbst_advance     USA   
1     POUSA0100835  lower               2022-01-05  herbst_advance     USA   
2     POUSA0109659  upper               2022-04-05  herbst_advance     USA   
3     POUSA0097391  lower               2021-12-01  herbst_advance     USA   
4          SE57501  lower               2021-12-02           avant      SE   
...            ...    ...                      ...             ...     ...   
8859       SE55760  lower               2021-09-27           avant      SE   
8860  POUSA0103529  upper               2022-02-03           avant     USA   
8861  POUSA0096814  lower               2021-11-27           avant     USA   
8862  POUSA0094264  lower               2021-11-02           avant     USA   
8863  POUSA0103177  lower               2022-01-29           avant     USA   

            batch       arch_cad_stage_2  \
0        10018225  POUSA0104682 {U2}.stl   
1        10018010  POUSA0100835 {L2}.stl   
2        10018491  POUSA0109659 {U2}.stl   
3        10017801  POUSA0097391 {L2}.stl   
4     46020211129       SE57501 {L2}.stl   
...           ...                    ...   
8859  46020210922       SE55760 {L2}.stl   
8860     10018161  POUSA0103529 {U2}.stl   
8861     10017770  POUSA0096814 {L2}.stl   
8862     10017618  POUSA0094264 {L2}.stl   
8863     10018144  POUSA0103177 {L2}.stl   

                                     relative_directory  \
0     herbst_advance/2022-02-16/USA/10018225/POUSA01...   
1     herbst_advance/2022-01-05/USA/10018010/POUSA01...   
2     herbst_advance/2022-04-05/USA/10018491/POUSA01...   
3     herbst_advance/2021-12-01/USA/10017801/POUSA00...   
4               avant/2021-12-02/SE/46020211129/SE57501   
...                                                 ...   
8859            avant/2021-09-27/SE/46020210922/SE55760   
8860         avant/2022-02-03/USA/10018161/POUSA0103529   
8861         avant/2021-11-27/USA/10017770/POUSA0096814   
8862         avant/2021-11-02/USA/10017618/POUSA0094264   
8863         avant/2022-01-29/USA/10018144/POUSA0103177   

                                 arch_cad_fit image_filename_hashed_anterior  \
0     features/POUSA0104682_upper_cad_fit.stl           1ceee12920b2cca5.bmp   
1     features/POUSA0100835_lower_cad_fit.stl           49e55514cb12bda1.bmp   
2     features/POUSA0109659_upper_cad_fit.stl           38d74317c90bc49d.bmp   
3     features/POUSA0097391_lower_cad_fit.stl           7bcef822566df689.bmp   
4          features/SE57501_lower_cad_fit.stl           0a469296e13793db.bmp   
...                                       ...                            ...   
8859       features/SE55760_lower_cad_fit.stl           695ce977053ee274.bmp   
8860  features/POUSA0103529_upper_cad_fit.stl           67c322ca606115c0.bmp   
8861  features/POUSA0096814_lower_cad_fit.stl           66fdb273e4a54d5a.bmp   
8862  features/POUSA0094264_lower_cad_fit.stl           30ab375db66b06f9.bmp   
8863  features/POUSA0103177_lower_cad_fit.stl           414d6782ff9fe24d.bmp   

                  filename  peak_value  first_cam_retention_anterior  
0     1ceee12920b2cca5.bmp        56.5                       52.2420  
1     49e55514cb12bda1.bmp       149.0                      145.4530  
2     38d74317c90bc49d.bmp        67.0                       64.8681  
3     7bcef822566df689.bmp        33.5                       32.6043  
4     0a469296e13793db.bmp        33.0                       32.3130  
...                    ...         ...                           ...  
8859  695ce977053ee274.bmp        64.0                       63.7499  
8860  67c322ca606115c0.bmp        64.5                       58.9450  
8861  66fdb273e4a54d5a.bmp        58.0                       57.2635  
8862  30ab375db66b06f9.bmp       108.5                      100.6180  
8863  414d6782ff9fe24d.bmp       103.5                       99.2478  

[8864 rows x 13 column

In [37]:
root_dir = Path('/ssd/dataset_som_retention')
# df = pd.read_csv(root_dir.joinpath('retention_dataset_2022_01_21.csv'))
# df
case = df.iloc[0]
case

case_id                                                                POUSA0104682
side                                                                          upper
first_cam_retention_date                                                 2022-02-16
product                                                              herbst_advance
country                                                                         USA
batch                                                                      10018225
arch_cad_stage_2                                              POUSA0104682 {U2}.stl
relative_directory                herbst_advance/2022-02-16/USA/10018225/POUSA01...
arch_cad_fit                                features/POUSA0104682_upper_cad_fit.stl
image_filename_hashed_anterior                                 1ceee12920b2cca5.bmp
filename                                                       1ceee12920b2cca5.bmp
peak_value                                                                  

In [38]:
path = root_dir.joinpath(case.relative_directory, case.arch_cad_stage_2)
print(path)
mesh = som.load_STL(root_dir.joinpath(case.relative_directory, case.arch_cad_stage_2))
print(mesh)

/ssd/dataset_som_retention/herbst_advance/2022-02-16/USA/10018225/POUSA0104682/POUSA0104682 {U2}.stl
SomnoMed.Trimesh (V1.8.2) 0x7fb95e6f8fd0: Faces = 267,960, Vertices = 133,981, Memory = 10.22 MiB


In [39]:
print(mesh.edges_nonunique.shape)
print(mesh.edges_unique.shape)
print(mesh.edges_unique_map.shape)
print(np.unique(mesh.edges_unique_map).shape)
print(mesh.edges_unique)
print(np.concatenate((mesh.edges_unique, mesh.edges_unique[:,::-1]), axis=0))


(803880, 2)
(401939, 2)
(803880,)
(401939,)
[[     0  18200]
 [     0  27646]
 [     0  62929]
 ...
 [133859 133873]
 [133860 133886]
 [133872 133933]]
[[     0  18200]
 [     0  27646]
 [     0  62929]
 ...
 [133873 133859]
 [133886 133860]
 [133933 133872]]


In [40]:
print("\n# Vertices: {}, {}".format(mesh.vertices, mesh.vertices.shape))
print("\n# Vertex normals: {}, {}".format(mesh.vertices_normal, mesh.vertices_normal.shape))
print("\n# Faces: {}, {}".format(mesh.faces, mesh.faces.shape))
print("\n# Edges: {}, {}".format(mesh.edges_unique, mesh.edges_unique.shape))
print("\n# Edges Length: {}, {}".format(mesh.edges_unique_length, mesh.edges_unique_length.shape))


# Vertices: [[-26.86976433   7.34505033  -5.06305599]
 [-20.96896362 -18.60492897  -1.5185554 ]
 [-13.76000214 -28.88738441   3.6235106 ]
 ...
 [-25.56417084 -14.2121315    5.10546112]
 [  1.96607339 -27.93789291  -4.00502634]
 [  3.2767942   34.12491608   5.10539913]], (133981, 3)

# Vertex normals: [[-3.69011141e-01  8.59039792e-01 -3.54797709e-01]
 [-4.00370923e-01  8.01879458e-01 -4.43500236e-01]
 [-6.52983659e-01 -7.56486011e-01 -3.66231683e-02]
 ...
 [ 1.56119970e-05  3.66741084e-05  9.99999999e-01]
 [ 9.96057795e-01  5.84870578e-02  6.66943266e-02]
 [ 3.09491746e-01 -8.46534929e-01  4.33120623e-01]], (133981, 3)

# Faces: [[ 26344  58969  77941]
 [ 46659  77941  58969]
 [ 26344  77941  86527]
 ...
 [ 25308 132002  14602]
 [ 46563  96323  25144]
 [126911  50488  96323]], (267960, 3)

# Edges: [[     0  18200]
 [     0  27646]
 [     0  62929]
 ...
 [133859 133873]
 [133860 133886]
 [133872 133933]], (401939, 2)

# Edges Length: [0.34990255 0.26068625 0.2403131  ... 0.03268846 0.

In [41]:
def assert_rd_frame(mesh, side, debug=False):
    mins = mesh.vertices.min(axis=0)
    maxs = mesh.vertices.max(axis=0)
    ranges = maxs - mins
    if debug:
        print(mins, maxs, ranges)
    
    ## Test if z-axis is correct
    # test z-range is smaller than x/y-range
    assert ranges[2] == ranges.min(), "z-axis in not aligned to OTP"
    # z-axis alignment
    assert ranges[2] <= 20, "z-axis thickness exceeds blank thickness"
    # z-axis polarity
    if side.lower() == 'lower':
        assert mesh.vertices_normal[:,2].mean() < 0, "z-axis is in the wrong direction"
    else:
        assert mesh.vertices_normal[:,2].mean() > 0, "z-axis is in the wrong direction"

    # Test if y-axis is posterior
    max_y = maxs[1]
    min_y = mins[1]
    x_at_max_y = mesh.vertices[np.where(mesh.vertices[:,1]==max_y)][0,0] 
    x_at_min_y = mesh.vertices[np.where(mesh.vertices[:,1]==min_y)][0,0] 

    assert abs(x_at_min_y) < 15, "Most anterior x-coord should be within +/-15mm of y-axis"
    assert abs(x_at_max_y) > 15, "Most posterior x-coord should be greater than +/-15mm from y-axis"

In [42]:
def gen_retention_hole_features(mesh, hole_coord):
    """ Generates the displacment from every vertex to a single retention hole
    
    inputs:
        mesh:
            fit surface mesh in rd frame, som.Trimesh
        hole_coord:
            Array of np.array([x, y, z]).
    outputs:
        v_to_hole_distances:
            distance (mm) from vertex to retention hole
        v_to_hole_normals:
            normals from vertex to retention holes
        
    """
    assert isinstance(hole_coord, np.ndarray)
    assert hole_coord.shape == (3,)

    # Only calculate x-y plane normals and lengths
    v_to_hole_vectors = hole_coord[:2]-mesh.vertices[:, :2]
    v_to_hole_distances = np.linalg.norm(v_to_hole_vectors, axis=1)
    v_to_hole_vectors_normals = v_to_hole_vectors/ v_to_hole_distances[:, np.newaxis]
    return v_to_hole_vectors_normals, v_to_hole_distances

In [43]:
case

case_id                                                                POUSA0104682
side                                                                          upper
first_cam_retention_date                                                 2022-02-16
product                                                              herbst_advance
country                                                                         USA
batch                                                                      10018225
arch_cad_stage_2                                              POUSA0104682 {U2}.stl
relative_directory                herbst_advance/2022-02-16/USA/10018225/POUSA01...
arch_cad_fit                                features/POUSA0104682_upper_cad_fit.stl
image_filename_hashed_anterior                                 1ceee12920b2cca5.bmp
filename                                                       1ceee12920b2cca5.bmp
peak_value                                                                  

In [45]:
%%time
import pymeshlab
import trimesh
from multiprocessing import Pool
desired_train_dataset_size=2000
desired_test_dataset_size=140
decimation=10000


# make dataset dir structure
dataset_name = 'binary_retention_10k'
paths = [
    f'datasets/{dataset_name}/high/train/',
    f'datasets/{dataset_name}/high/test/',
    f'datasets/{dataset_name}/good/train/',
    f'datasets/{dataset_name}/good/test/',
]
for path in paths:
    os.makedirs(path, exist_ok=True)



def process_row(root_dir, row, train_test):
    case_dir = root_dir.joinpath(row.relative_directory)
    if row.peak_value > 70:
        label='high'
    else:
        label='good'
    path = f'datasets/{dataset_name}/{label}/{train_test}/{row.case_id}_{row.side.lower()}_{round(row.peak_value)}.obj'
    try:
        mesh = trimesh.load(case_dir.joinpath(row.arch_cad_stage_2))
        # assert_rd_frame(mesh, row.side.lower(), debug=False)
        if mesh is None:# or scan_mesh is None:
            return
    except Exception as err:
        print(err)
        return
        
    # DECIMATION
    if decimation != 0:
        mesh = mesh.simplify_quadratic_decimation(decimation)
        

    # if row.side.lower() == 'upper':
    #     # Flip uppers to face upwards like a lower
    #     transform = som.Transform(rotation=(0,180,0), degrees=True)
    #     mesh.apply_transform(transform)

    
    # Stage 1 cleaning
    trimesh.repair.fix_inversion(mesh)
    trimesh.repair.fill_holes(mesh)
    trimesh.repair.fix_normals(mesh)
    mesh.export(path)
    
    # Stage 2 cleaning
    ms = pymeshlab.MeshSet()
    ms.load_new_mesh(str(path))
    ms.meshing_remove_null_faces()
    ms.meshing_remove_duplicate_faces()
    ms.meshing_remove_duplicate_vertices()
    ms.meshing_repair_non_manifold_edges(method='Remove Faces')
    ms.meshing_repair_non_manifold_vertices()
    ms.meshing_remove_connected_component_by_face_number(mincomponentsize=int(decimation*0.9), removeunref=True)
    ms.meshing_remove_unreferenced_vertices()
    ms.save_current_mesh(str(path))
    ms.clear()
    
    
    # Print results
    mesh = som.load(path)
    final_result = str("{} {} {} {} {} {} {}: {}".format(mesh.is_connected, mesh.is_closed,  mesh.is_watertight, mesh.is_self_intersecting, mesh.is_smooth, mesh.is_manifold, len(mesh.split()), path))
    print(final_result)
    
    if len(mesh.edges_unique) != int(decimation*1.5) or not mesh.is_manifold or not mesh.is_closed:
        os.remove(path)
        

args = []
count = 0
for _, row in df.iterrows():
    if count < desired_train_dataset_size:
        args.append((root_dir, row, 'train'))
    elif count < desired_train_dataset_size+desired_test_dataset_size:
        args.append((root_dir, row, 'test'))
    else:
        break
    count +=1

print(len(args))
# for arg in args:
#     print(arg[0], arg[2])
#     assert(len(arg)==3)
#     assert(type(arg[0]) != bool)
#     assert(type(arg[1]) != bool)
#     assert(type(arg[2]) != bool)

with Pool(processes=48) as pool:
    pool.starmap(process_row, args)

    


2140
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI bac

In [46]:
shrec_dir =  Path('datasets/shrec_16')

for path in shrec_dir.glob("*/*/*.obj"):
    mesh = som.load(path)
    final_result = str("{} {} {} {} {} {} {}: {} : {}".format(mesh.is_connected, mesh.is_closed,  mesh.is_watertight, mesh.is_self_intersecting, mesh.is_smooth, mesh.is_manifold, len(mesh.split()), path, mesh))
    print(final_result)
    


True True False True False True 1: datasets/shrec_16/bird2/train/T83.obj : SomnoMed.Trimesh (V1.8.2) 0x7fb91d267b50: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T130.obj : SomnoMed.Trimesh (V1.8.2) 0x7fb95e763e20: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T584.obj : SomnoMed.Trimesh (V1.8.2) 0x7fb91d0c2f10: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T417.obj : SomnoMed.Trimesh (V1.8.2) 0x7fb95e763250: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T520.obj : SomnoMed.Trimesh (V1.8.2) 0x7fb91d0c2eb0: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T500.obj : SomnoMed.Trimesh (V1.8.2) 0x7fb95e763e20: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True F

In [ ]:

shrec_dir =  Path('datasets/binary_retention_10k')

for path in shrec_dir.glob("*/*/*.obj"):
    mesh = som.load(path)
    final_result = str("{} {} {} {} {} {} {}: {} {}: {}".format(mesh.is_connected, mesh.is_closed,  mesh.is_watertight, mesh.is_self_intersecting, mesh.is_smooth, mesh.is_manifold, len(mesh.split()), len(mesh.edges_unique), path, mesh))
    print(final_result)

True True False True False True 1: 15000 datasets/binary_retention_10k/high/train/POAUS0030342_upper_114.obj: SomnoMed.Trimesh (V1.8.2) 0x7fb8a30b9e80: Faces = 10,000, Vertices = 5,002, Memory = 0.84 MiB
True True False True False True 1: 15000 datasets/binary_retention_10k/high/train/nl173055_upper_125.obj: SomnoMed.Trimesh (V1.8.2) 0x7fb8a30b9fd0: Faces = 10,000, Vertices = 5,002, Memory = 0.84 MiB
True True False True False True 1: 15000 datasets/binary_retention_10k/high/train/nl177273_upper_160.obj: SomnoMed.Trimesh (V1.8.2) 0x7fb91aca28e0: Faces = 10,000, Vertices = 5,002, Memory = 0.84 MiB
True True False True False True 1: 15000 datasets/binary_retention_10k/high/train/POUSA0105750_upper_130.obj: SomnoMed.Trimesh (V1.8.2) 0x7fb8a30b9eb0: Faces = 10,000, Vertices = 5,002, Memory = 0.84 MiB
True True False True False True 1: 15000 datasets/binary_retention_10k/high/train/POUSA0091066_upper_150.obj: SomnoMed.Trimesh (V1.8.2) 0x7fb91aca28e0: Faces = 10,000, Vertices = 5,002, Memory

In [48]:
case_dir = root_dir.joinpath(case.relative_directory)
mesh_path = case_dir.joinpath(case.arch_cad_stage_2)

mesh = trimesh.load(mesh_path)
mesh.show()

/home/josh/.local/lib/python3.8/site-packages/IPython/core/display.py:419: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [49]:
print(mesh)
dec_mesh = mesh.simplify_quadratic_decimation(2000)
print(len(dec_mesh.edges_unique))
dec_mesh.show()

<trimesh.Trimesh(vertices.shape=(133981, 3), faces.shape=(267960, 3))>
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
3000


/home/josh/.local/lib/python3.8/site-packages/IPython/core/display.py:419: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")
